#  DATA VISUALIZATION PROJECT

## IMPORT LIBRARIES 

In [ ]:
!pip install psycopg2

In [ ]:
import re
import time
import requests
import pandas as pd
from bs4 import BeautifulSoup
import psycopg2
from psycopg2.errors import UniqueViolation
from sqlalchemy import create_engine
import ssl

## FUNCTIONS

In [ ]:
def getcomp(year_comp, pag=1):
    '''
    year_comp is the year when competition was done

    Its return is a object soup. It´s a kind of html conteiner based an answer from server
    or can be a integer -1 when there is no information for that year


    '''  
    ssl._create_default_https_context = ssl._create_unverified_context
    get_html = requests.get(f'https://worldathletics.org/records/competition-performance-rankings?type=2&year={year_comp}&sortBy=score&page={pag}')
    html = get_html.content
    soup = BeautifulSoup(html)
    list_results = soup.find_all('h2', attrs = {'class' : 'no-results'})
    if len(list_results) > 0:
        return -1
    return [soup, pag]



In [ ]:
def atualiza_prova_compet(cursor, cod_prova, cod_competicao, score_prova_competicao,data_prova_competicao):
    try: 
        print(f'Inserindo competicao {cod_competicao} e prova {cod_prova}')
        cursor.execute(f"INSERT INTO tb_prova_competicao (cod_prova, cod_competicao, score_prova_competicao,data_prova_competicao)" \
                       f"VALUES ({cod_prova}, {cod_competicao[0]}, {score_prova_competicao},'{data_prova_competicao}')")

    except UniqueViolation:
        print ("prova ja existe na competicao")
                    

In [ ]:
def atualiza_atleta_prova_competicao(cursor,cod_prova, cod_competicao, lista_tb_atleta_competicao):
    cursor.execute(f"select cod_prova_competicao from tb_prova_competicao where cod_prova = {cod_prova} and cod_competicao = {cod_competicao[0]}")
    cod_prova_competicao = cursor.fetchone()[0] 
    for x in lista_tb_atleta_competicao:
        try:
            print(f'Inserindo atleta {x[0]}')
            cursor.execute(f"INSERT INTO tb_atleta_prova_competicao (cod_atleta, cod_prova_competicao, result, score)" \
                         f"VALUES ({x[0]}, {cod_prova_competicao}, '{x[1]}', {x[2]})")
        except UniqueViolation:
            print ("atleta ja existe na prova")

            

            

In [ ]:
def atualiza_atleta(cursor,cod_atleta, lista_tb_atleta_competicao):
   
    for x in lista_tb_atleta_competicao:
        try:
            print(f'Inserindo atleta na tb_atleta {x[0]}')
            cursor.execute(f"INSERT INTO tb_atleta (cod_atleta)" \
                         f"VALUES ({x[0]})")
        except UniqueViolation:
            print ("atleta ja existe na tb_atleta")

## Insertions on tb_competicao

In [ ]:
connection = psycopg2.connect(user="postgres",
                                  password="jujuba11",
                                  host="127.0.0.1",
                                  port="5432",
                                  database="db_atletismo",
                                  options="-c search_path=db_atl")


connection.autocommit = True
cursor = connection.cursor()
contador = 0
list_results = []
year= 2019
soup = getcomp(year,1)[0]
pagina = getcomp(year,1)[1]   
last_page = int(soup.find_all('a', attrs = {'class' : 'btn--pagination btn--pag-last pag-control'})[0]['data-page'])
list_competicao = soup.find_all('tbody')[0].find_all('tr')

if last_page > 0:
    for pagina_int in range(last_page):
        pagina_int += 1
        soup = getcomp(year,pagina_int)[0]
        pagina = getcomp(year,pagina_int)[1]   
        list_competicao = soup.find_all('tbody')[0].find_all('tr')
    
        time.sleep(5)

        for line in range(len(list_competicao)-1):
            try:
                cod_competicao = re.findall(r'\d+',list_competicao[line]['data-href'])[0]
                place = list_competicao[line].find_all('td')[0].text.strip()
                #  competition = list_competicao[line].find_all('td')[1].text.strip()
            
                tamanho = len(list_competicao[line].find_all('td')[1].text.strip().split(","))
            
                lista_nome_competicao = list_competicao[line].find_all('td')[1].text.strip().split(",")
                nome_competicao = " ".join(re.findall("[a-zA-Z]+", lista_nome_competicao[0].strip()))
                cidade_competicao =  " ".join(re.findall("[a-zA-Z]+", lista_nome_competicao[len(lista_nome_competicao)-1].strip()))
                   
         
                country = list_competicao[line].find_all('td')[2].text.strip()
                Start_date = list_competicao[line].find_all('td')[3].text.strip()
                end_date = list_competicao[line].find_all('td')[4].text.strip()
                part_score = list_competicao[line].find_all('td')[5].text.strip()
                ps_place = list_competicao[line].find_all('td')[6].text.strip()
                result_score = list_competicao[line].find_all('td')[7].text.strip()
                rs_place = list_competicao[line].find_all('td')[8].text.strip()
       
                if pagina == 1:
                   comp_score = list_competicao[line].find_all('td')[10].text.strip()
                else:
                    comp_score = list_competicao[line].find_all('td')[9].text.strip()
             
                list_results.append((cod_competicao, nome_competicao, comp_score, part_score, result_score, Start_date, end_date,
                                  cidade_competicao, country, ps_place, rs_place ))
            
            
                sql_update = f"INSERT INTO tb_competicao (cod_competicao, nome_competição, score_competicao," \
                    f"score_participacao_competicao, score_result_competicao, data_inicial_competicao," \
                    f"data_final_competicao, cidade_competicao, pais_competicao," \
                    f"ps_place_competicao, rs_place_competicao)" \
                    f" VALUES ({cod_competicao},'{nome_competicao}','{comp_score}','{part_score}','{result_score}','{Start_date}','{end_date}', "\
                    f"'{cidade_competicao}','{country}','{ps_place}','{rs_place}')"
                contador += 1  
                print (f'Executando Query {contador} executada')
                cursor.execute(sql_update)
        
           # except UniqueViolation:
           #     print("Registro encontrado")
           #     continue     ''' 
            
            except (Exception, psycopg2.DatabaseError) as error:
                print("Error in transction Reverting all other operations of a transction ", error)
    

print("Transaction completed successfully ")
if connection:
    connection.commit()
    cursor.close()
    connection.close()
    print("PostgreSQL connection is closed")
    
     

## Insertions on other tables

In [10]:
connection = psycopg2.connect(user="postgres",
                                  password="jujuba11",
                                  host="127.0.0.1",
                                  port="5432",
                                  database="db_atletismo",
                                  options="-c search_path=db_atl")


connection.autocommit = True
cursor = connection.cursor()

cursor.execute(f"SELECT cod_competicao  FROM tb_competicao WHERE date_part('year', data_final_competicao) = {year};")
               
list_cod_comp = cursor.fetchall()   

ssl._create_default_https_context = ssl._create_unverified_context

lista_full = []

for compt in list_cod_comp:
    get_html = requests.get(f'https://worldathletics.org/records/competition-performance-rankings/ranking/{compt[0]}')
    print (f'https://worldathletics.org/records/competition-performance-rankings/ranking/{compt[0]}')
    html = get_html.content
    soup = BeautifulSoup(html)
    list_results = soup.find_all('div', attrs = {'class' : 'cpr-result-score'})

    list_competicao = soup.find_all('tbody')[0].find_all('tr')

    for i in list_results:
        try:
            prova = i.find_all('h3')[0].text.split("'s")
            print (f'Prova {prova[0]} na modalidade {prova[1]}')
            score_prova =i.find_all('p')[0].text.split(":")
            cursor.execute(f"INSERT INTO tb_prova (nome_prova, genero_prova) VALUES ('{prova[1]}', '{prova[0]}')")
            
            cursor.execute(f"SELECT cod_prova  FROM tb_prova WHERE nome_prova='{prova[1]}' and genero_prova='{prova[0]}';")
               
            cod_prova = cursor.fetchone()        
            print (f'codigo  da prova {cod_prova[0]}')         
            lista_tb_atleta_competicao = []
            for x in i.find_all('tbody')[0].find_all('tr'):
                score = x.find_all('td')[0].text
                result = x.find_all('td')[1].text
                date = x.find_all('td')[2].text
                cod_atleta = re.findall(r'\d+', x.find_all('td')[3].find_all('span')[0]['data-href'])[0]
                lista_full.append((cod_prova[0],score_prova[1].strip(), score.strip(), result.strip(), date.strip(), cod_atleta.strip()))    
                lista_tb_atleta_competicao.append([cod_atleta,result,score])
            atualiza_prova_compet(cursor, cod_prova[0],compt,score_prova[1], date.strip())
            atualiza_atleta(cursor,cod_atleta, lista_tb_atleta_competicao)
            atualiza_atleta_prova_competicao(cursor,cod_prova[0],compt,lista_tb_atleta_competicao)
        
        except IndexError:
            break
        except UniqueViolation:
            print ("Prova ja existe")
            cursor.execute(f"SELECT cod_prova  FROM tb_prova WHERE nome_prova='{prova[1]}' and genero_prova='{prova[0]}';")
            cod_prova = cursor.fetchone()        
            print (f'codigo  da prova {cod_prova[0]}')         
            lista_tb_atleta_competicao = []
            for x in i.find_all('tbody')[0].find_all('tr'):
                try:
                    score = x.find_all('td')[0].text
                    result = x.find_all('td')[1].text
                    date = x.find_all('td')[2].text
                    cod_atleta = re.findall(r'\d+', x.find_all('td')[3].find_all('span')[0]['data-href'])[0]
                    lista_full.append((cod_prova[0],score_prova[1].strip(), score.strip(), result.strip(), date.strip(), cod_atleta.strip()))   
                    lista_tb_atleta_competicao.append([cod_atleta,result,score])
                except IndexError:
                    break
            
            atualiza_prova_compet(cursor, cod_prova[0],compt,score_prova[1], date.strip())
            atualiza_atleta(cursor,cod_atleta, lista_tb_atleta_competicao)
            atualiza_atleta_prova_competicao(cursor,cod_prova[0],compt,lista_tb_atleta_competicao)
            continue
if connection:
    connection.commit()
    cursor.close()
    connection.close()
    print("PostgreSQL connection is closed")


Inserindo atleta 014614328
Inserindo atleta 014761688
Inserindo atleta 014703372
Inserindo atleta 014614267
Prova Women na modalidade  200 Metres
Prova ja existe
codigo  da prova 68
Inserindo competicao (588841,) e prova 68
Inserindo atleta na tb_atleta 014774694
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014582264
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014788998
Inserindo atleta na tb_atleta 014840686
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014841405
Inserindo atleta 014774694
Inserindo atleta 014582264
Inserindo atleta 014788998
Inserindo atleta 014840686
Inserindo atleta 014841405
Prova Men na modalidade  400 Metres
Prova ja existe
codigo  da prova 5
Inserindo competicao (588841,) e prova 5
Inserindo atleta na tb_atleta 014790020
Inserindo atleta na tb_atleta 014658131
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014780902
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014846480
atleta ja existe n

https://worldathletics.org/records/competition-performance-rankings/ranking/590548
Prova Women na modalidade  100 Metres Hurdles
Prova ja existe
codigo  da prova 9
Inserindo competicao (590548,) e prova 9
Inserindo atleta na tb_atleta 014259379
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014408972
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014408971
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014515442
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014260311
atleta ja existe na tb_atleta
Inserindo atleta 014259379
Inserindo atleta 014408972
Inserindo atleta 014408971
Inserindo atleta 014515442
Inserindo atleta 014260311
Prova Women na modalidade  800 Metres
Prova ja existe
codigo  da prova 24
Inserindo competicao (590548,) e prova 24
Inserindo atleta na tb_atleta 014477412
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014757954
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014592927
atleta ja exis

Inserindo atleta 014679092
Prova Women na modalidade  400 Metres
Prova ja existe
codigo  da prova 11
Inserindo competicao (590728,) e prova 11
Inserindo atleta na tb_atleta 014831346
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014753311
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014855928
Inserindo atleta na tb_atleta 014849130
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014630030
Inserindo atleta 014831346
Inserindo atleta 014753311
Inserindo atleta 014855928
Inserindo atleta 014849130
Inserindo atleta 014630030
Prova Men na modalidade  800 Metres
Prova ja existe
codigo  da prova 19
Inserindo competicao (590728,) e prova 19
Inserindo atleta na tb_atleta 014406134
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014568166
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014844398
Inserindo atleta na tb_atleta 014803266
Inserindo atleta na tb_atleta 014715556
atleta ja existe na tb_atleta
Inserindo atleta 014406134
I

https://worldathletics.org/records/competition-performance-rankings/ranking/591673
Prova Women na modalidade  400 Metres
Prova ja existe
codigo  da prova 11
Inserindo competicao (591673,) e prova 11
Inserindo atleta na tb_atleta 014637147
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014336067
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014633739
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014518726
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014739088
atleta ja existe na tb_atleta
Inserindo atleta 014637147
Inserindo atleta 014336067
Inserindo atleta 014633739
Inserindo atleta 014518726
Inserindo atleta 014739088
Prova Men na modalidade  Hammer Throw
Prova ja existe
codigo  da prova 202
Inserindo competicao (591673,) e prova 202
Inserindo atleta na tb_atleta 014365669
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014465491
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014169488
atleta ja existe n

codigo  da prova 24
Inserindo competicao (589613,) e prova 24
Inserindo atleta na tb_atleta 014751161
Inserindo atleta na tb_atleta 014784501
Inserindo atleta na tb_atleta 014746779
Inserindo atleta na tb_atleta 014827922
Inserindo atleta na tb_atleta 014694574
Inserindo atleta 014751161
Inserindo atleta 014784501
Inserindo atleta 014746779
Inserindo atleta 014827922
Inserindo atleta 014694574
Prova Women na modalidade  1500 Metres
Prova ja existe
codigo  da prova 8
Inserindo competicao (589613,) e prova 8
Inserindo atleta na tb_atleta 014694574
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014751161
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014816092
Inserindo atleta na tb_atleta 014746772
Inserindo atleta na tb_atleta 014883038
Inserindo atleta 014694574
Inserindo atleta 014751161
Inserindo atleta 014816092
Inserindo atleta 014746772
Inserindo atleta 014883038
Prova Women na modalidade  Long Jump
Prova ja existe
codigo  da prova 246
Inserindo competica

...

Inserindo atleta 014719981
Inserindo atleta 014879357
Inserindo atleta 014803859
Inserindo atleta 014723917
Prova Men na modalidade  3000 Metres Steeplechase
Prova ja existe
codigo  da prova 1
Inserindo competicao (590195,) e prova 1
Inserindo atleta na tb_atleta 014688342
Inserindo atleta na tb_atleta 014877099
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014835312
Inserindo atleta na tb_atleta 014834142
Inserindo atleta 014688342
Inserindo atleta 014877099
Inserindo atleta 014835312
Inserindo atleta 014834142
https://worldathletics.org/records/competition-performance-rankings/ranking/588503
Prova Men na modalidade  100 Metres
Prova ja existe
codigo  da prova 13
Inserindo competicao (588503,) e prova 13
Inserindo atleta na tb_atleta 014744137
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014782133
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014246576
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014877700
atleta ja existe na t

Inserindo atleta na tb_atleta 014832082
Inserindo atleta 014673059
Inserindo atleta 014372136
Inserindo atleta 014874325
Inserindo atleta 014647587
Inserindo atleta 014832082
Prova Men na modalidade  200 Metres
Prova ja existe
codigo  da prova 2
Inserindo competicao (592291,) e prova 2
Inserindo atleta na tb_atleta 014820041
Inserindo atleta na tb_atleta 014819633
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014779575
Inserindo atleta na tb_atleta 014804180
Inserindo atleta na tb_atleta 014804182
Inserindo atleta 014820041
Inserindo atleta 014819633
Inserindo atleta 014779575
Inserindo atleta 014804180
Inserindo atleta 014804182
Prova Women na modalidade  Shot Put
Prova ja existe
codigo  da prova 72
Inserindo competicao (592291,) e prova 72
Inserindo atleta na tb_atleta 014876206
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014863757
Inserindo atleta na tb_atleta 014877617
Inserindo atleta na tb_atleta 014820060
Inserindo atleta na tb_atleta 014876942
Inse

https://worldathletics.org/records/competition-performance-rankings/ranking/591861
Prova Men na modalidade  Long Jump
Prova ja existe
codigo  da prova 108
Inserindo competicao (591861,) e prova 108
Inserindo atleta na tb_atleta 014572528
Inserindo atleta na tb_atleta 014597393
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014652422
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014198934
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014842377
Inserindo atleta 014572528
Inserindo atleta 014597393
Inserindo atleta 014652422
Inserindo atleta 014198934
Inserindo atleta 014842377
Prova Women na modalidade  1500 Metres
Prova ja existe
codigo  da prova 8
Inserindo competicao (591861,) e prova 8
Inserindo atleta na tb_atleta 014408753
Inserindo atleta na tb_atleta 014635018
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014479064
Inserindo atleta na tb_atleta 014752423
Inserindo atleta na tb_atleta 014801027
Inserindo atleta 014408753
Inser

https://worldathletics.org/records/competition-performance-rankings/ranking/591330
Prova Women na modalidade  Triple Jump
Prova ja existe
codigo  da prova 285
Inserindo competicao (591330,) e prova 285
Inserindo atleta na tb_atleta 014456805
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014589868
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014452679
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014504733
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014777723
atleta ja existe na tb_atleta
Inserindo atleta 014456805
Inserindo atleta 014589868
Inserindo atleta 014452679
Inserindo atleta 014504733
Inserindo atleta 014777723
Prova Women na modalidade  Long Jump
Prova ja existe
codigo  da prova 246
Inserindo competicao (591330,) e prova 246
Inserindo atleta na tb_atleta 014504733
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014456805
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014753516
Inserindo atleta

Prova Women na modalidade  100 Metres
Prova ja existe
codigo  da prova 7
Inserindo competicao (592487,) e prova 7
Inserindo atleta na tb_atleta 014400466
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014709180
Inserindo atleta na tb_atleta 014566301
Inserindo atleta na tb_atleta 014733792
atleta ja existe na tb_atleta
Inserindo atleta 014400466
Inserindo atleta 014709180
Inserindo atleta 014566301
Inserindo atleta 014733792
Prova Men na modalidade  200 Metres
Prova ja existe
codigo  da prova 2
Inserindo competicao (592487,) e prova 2
Inserindo atleta na tb_atleta 014511034
atleta ja existe na tb_atleta
Inserindo atleta na tb_atleta 014685549
Inserindo atleta na tb_atleta 014912093
Inserindo atleta na tb_atleta 014376975
Inserindo atleta 014511034
Inserindo atleta 014685549
Inserindo atleta 014912093
Inserindo atleta 014376975
Prova Women na modalidade  400 Metres Hurdles
Prova ja existe
codigo  da prova 10
Inserindo competicao (592487,) e prova 10
Inserindo atleta na tb_a